In [1]:
import pandas as pd
from ch2.data import *
from ch2.squeal.database import connect

s = session('-v 0')
raw = activity_statistics(s, SPEED, DISTANCE, ELEVATION, CADENCE, LATITUDE, LONGITUDE, HEART_RATE,
                         local_time='2018-01-16 12:00', activity_group_name='Bike', with_timespan=True)
raw.describe()

Timespan ID     Latitude    Longitude        Speed      Distance  \
count   2311.000000  2311.000000  2311.000000  2311.000000   2311.000000   
mean   15892.517525   -33.344065   -70.503079     5.776180  38091.234479   
std        7.501256     0.037118     0.047217     2.359839  20038.745664   
min    15817.000000   -33.427446   -70.611250     0.000000      4.860000   
25%    15886.500000   -33.377510   -70.538338     4.576500  22816.870000   
50%    15894.000000   -33.331681   -70.477016     5.822000  39342.380000   
75%    15895.000000   -33.314070   -70.470489     7.161500  52234.785000   
max    15906.000000   -33.289474   -70.453889    14.229000  75357.890000   

           Cadence   Heart Rate    Elevation  
count  2308.000000  2311.000000  2287.000000  
mean     59.011265   121.017309  1135.107528  
std      45.584932    11.830793   396.117057  
min       0.000000    82.000000   616.376105  
25%       0.000000   113.000000   762.764162  
50%      86.500000   121.000000  1035.741355  
75%      98.000000   129.000000  1524.340278  
max     125.000000   153.000000  1814.388717

In [2]:
from ch2.data.power import *

df = linear_resample(raw)
df = add_differentials(df)
df = add_energy_budget(df, m=64+12)
df = add_air_speed(df, 0, 0)
df = add_loss_estimate(df)
df = add_power_estimate(df)
print(measure_initial_scaling(df))
df = add_modeled_hr(df, int(0.5 + 30 * 60 / median_dt(df)), 0.05, 120, 45)


(0.05454193739150711, 119.93531713733339, 45.0)


In [3]:
model = fit_power(df, PowerModel(cda=0.45, slope=0.05, intercept=120, delay=45), 
                  'slope', 'intercept', 'delay')
print(model)

/home/andrew/project/ch2/choochoo/env/lib/python3.7/site-packages/scipy/stats/stats.py:4653: RuntimeWarning: divide by zero encountered in true_divide
  terms = (f_obs - f_exp)**2 / f_exp


PowerModel(cda=0.45, crr=0, slope=0.056805885150528826, intercept=119.97785550215892, window=1800, delay=45.0, m=70, wind_speed=0, wind_heading=0)


In [8]:
df = add_modeled_hr(df, 360, 0.056, 120, 45)

In [9]:
from bokeh.plotting import output_notebook, show
from bokeh.layouts import row, column

from ch2.data.plot import *

output_notebook()
df['error'] = df[DETRENDED_HEART_RATE] - df[PREDICTED_HEART_RATE]
show(column([comparison_line_plot(700, 200, TIME, y, df) 
             for y in (POWER, HEART_RATE, DETRENDED_HEART_RATE, PREDICTED_HEART_RATE, 'error')]))


Loading BokehJS ...

In [6]:
print(1800 / median_dt(df))
df[HEART_RATE].rolling(360, center=True, min_periods=1).median()

360.0


2018-01-16 10:09:32+00:00    120.000000
2018-01-16 10:09:37+00:00    120.000000
2018-01-16 10:09:42+00:00    120.000000
2018-01-16 10:09:47+00:00    120.000000
2018-01-16 10:09:52+00:00    120.000000
2018-01-16 10:09:57+00:00    120.000000
2018-01-16 10:10:02+00:00    120.000000
2018-01-16 10:10:07+00:00    120.000000
2018-01-16 10:10:12+00:00    120.000000
2018-01-16 10:10:17+00:00    120.000000
2018-01-16 10:10:22+00:00    120.050000
2018-01-16 10:10:27+00:00    120.100000
2018-01-16 10:10:32+00:00    120.100000
2018-01-16 10:10:37+00:00    120.100000
2018-01-16 10:10:42+00:00    120.175000
2018-01-16 10:10:47+00:00    120.250000
2018-01-16 10:10:52+00:00    120.267857
2018-01-16 10:10:57+00:00    120.250000
2018-01-16 10:11:02+00:00    120.196429
2018-01-16 10:11:07+00:00    120.142857
2018-01-16 10:11:12+00:00    120.121429
2018-01-16 10:11:17+00:00    120.100000
2018-01-16 10:11:22+00:00    120.100000
2018-01-16 10:11:27+00:00    120.100000
2018-01-16 10:11:32+00:00    120.050000
